In [ ]:
"""
Copyright 2021 Aonghus McGovern

This file is part of Music_Image_Matcher_Notebooks_And_Writeup.

Music_Image_Matcher_Notebooks_And_Writeup is free software: you can redistribute it and/or modify it under the terms of the 
GNU General Public License as published by the Free Software Foundation, either version 3 of the License, or (at your option) 
any later version.

Music_Image_Matcher_Notebooks_And_Writeup is distributed in the hope that it will be useful, but WITHOUT ANY WARRANTY; 
without even the implied warranty of MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the GNU General Public License 
for more details.

You should have received a copy of the GNU General Public License along with Music_Image_Matcher_Notebooks_And_Writeup.  
If not, see <https://www.gnu.org/licenses/>.
"""

In [1]:
import fileinput
import math
import matplotlib.pyplot as plt
import numpy as np
import operator
import os
import pandas as pd
import pickle
from PIL import Image
import torchvision.transforms as transforms
from sklearn.decomposition import PCA
from sklearn.metrics import mean_squared_error, accuracy_score
from sklearn.metrics.pairwise import pairwise_distances
import time
import torch
import torchvision.models as models
import torch.nn as nn

In [2]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [3]:
oramas_data = pd.read_csv('oramas_data_with_categories_and_labels.csv')

In [4]:
oramas_data['tempo_category'] = pd.qcut(oramas_data['Tempo'], q = 5, labels = ['very slow', 'slow', 'medium', 'fast',
                                                                              'very fast'])

In [5]:
# Load FairFace dataset
face_test_folder = 'C:/Users/amcgo/Documents/Images_To_Music/Music_Image_Matcher/Face test dataset/'

face_dataset = pd.read_csv(face_test_folder+'fairface_label_train.csv').append(pd.read_csv(face_test_folder+'fairface_label_val.csv'))

In [6]:
# Use the same code as in the 'Create_Content_And_Style_Matrices.ipynb'
class Normalization(nn.Module):
    def __init__(self, mean, std):
        super(Normalization, self).__init__()
        # .view the mean and std to make them [C x 1 x 1] so that they can
        # directly work with image Tensor of shape [B x C x H x W].
        # B is batch size. C is number of channels. H is height and W is width.
        self.mean = torch.tensor(mean).view(-1, 1, 1)
        self.std = torch.tensor(std).view(-1, 1, 1)

    def forward(self, img):
        # normalize img
        return (img - self.mean) / self.std

def get_content_matrix(target): 

    target = target.detach()
    
    reshaped = torch.reshape(target, (128, 12544))
                
    pca = PCA(n_components=50)
    pca.fit(reshaped)

    reduced = pca.fit_transform(reshaped)
    return reduced
    
def get_style_matrix(target_feature):
    target = gram_matrix(target_feature).detach()       
    pca = PCA(n_components=15)
    pca.fit(target)
                
    reduced = pca.fit_transform(target)
    return reduced

def get_image(image_path, reshape_size = (224,224)):
    transform = transforms.Compose([transforms.Resize(reshape_size),
    transforms.ToTensor(), transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])])
    
    image = Image.open(open(image_path, 'rb'))
    if image.mode == 'RGB':
        try:
            return transform(image)
        except:
            return None
    else:
        return None
    
def gram_matrix(input):
    a, b, c, d = input.size()  # a=batch size(=1)
    # b=number of feature maps
    # (c,d)=dimensions of a f. map (N=c*d)

    features = input.view(a * b, c * d)  # resise F_XL into \hat F_XL

    G = torch.mm(features, features.t())  # compute the gram product

    # we 'normalize' the values of the gram matrix
    # by dividing by the number of element in each feature maps.
    return G.div(a * b * c * d)

def imshow(inp, title=None):
    """Imshow for Tensor."""
    inp = inp.numpy().transpose((1, 2, 0))
    mean = np.array([0.485, 0.456, 0.406])
    std = np.array([0.229, 0.224, 0.225])
    inp = std * inp + mean
    inp = np.clip(inp, 0, 1)
    plt.imshow(inp)
    if title is not None:
        plt.title(title)
    plt.pause(0.001)  # pause a bit so that plots are updated
    
def get_image(image_path):
    transform = transforms.Compose([transforms.Resize((224, 224)),
    transforms.ToTensor(), transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])])
    
    image = Image.open(open(image_path, 'rb'))
    if image.mode == 'RGB':
        try:
            return transform(image)
        except:
            return None
    else:
        return None

def get_style_model_and_losses(style_img, content_img, cnn = models.vgg19(pretrained=True).features.to(device).eval(), 
                               normalization_mean = torch.tensor([0.485, 0.456, 0.406]).to(device),
normalization_std = torch.tensor([0.229, 0.224, 0.225]).to(device),  content_layers=['conv_4'],  
                               style_layers=['conv_1', 'conv_2', 'conv_3', 'conv_4', 'conv_5']):
    # normalization module
    normalization = Normalization(normalization_mean, normalization_std).to(device)

    # just in order to have an iterable access to or list of content/syle
    # losses
    content_matrices = list()
    style_matrices = list()

    # assuming that cnn is a nn.Sequential, so we make a new nn.Sequential
    # to put in modules that are supposed to be activated sequentially
    model = nn.Sequential(normalization)

    i = 0  # increment every time we see a conv
    for layer in cnn.children():
        if isinstance(layer, nn.Conv2d):
            i += 1
            name = 'conv_{}'.format(i)
        elif isinstance(layer, nn.ReLU):
            name = 'relu_{}'.format(i)
            # The in-place version doesn't play very nicely with the ContentLoss
            # and StyleLoss we insert below. So we replace with out-of-place
            # ones here.
            layer = nn.ReLU(inplace=False)
        elif isinstance(layer, nn.MaxPool2d):
            name = 'pool_{}'.format(i)
        elif isinstance(layer, nn.BatchNorm2d):
            name = 'bn_{}'.format(i)
        else:
            raise RuntimeError('Unrecognized layer: {}'.format(layer.__class__.__name__))
            
        model.add_module(name, layer)
        
        if name in content_layers:
            # add content loss:
            target = model(content_img).detach()
            content_matrices.append(get_content_matrix(target))
            

        if name in style_layers:
            # add style loss:
            target_feature = model(style_img).detach()
            style_matrices.append(get_style_matrix(target_feature))
            
    return style_matrices, content_matrices

# Declare a function that takes an image and returns the images that are most similar
# The number of images returned is controlled by the 'number_matches' parameter
def get_closest(image, comparison_album_indexes, comparison_content_matrices, comparison_style_matrices,
               number_matches):
    # Get the style and content matrices for the image
    style_matrices, content_matrices = get_style_model_and_losses(image, image)
    # Unroll the content matrix into a single row
    test_content_matrix = [np.reshape(content_matrices, (6400,))]
    # Combine the style matrices and unroll the combined matrix into a single row
    test_style_matrix = [np.reshape(np.concatenate(style_matrices), (9600,))]
    # Get the distance between the image's content matrix and the content matrices of the comparison images
    content_pairwise_distances = pairwise_distances(test_content_matrix, comparison_content_matrices)
    # Get the distance between the image's style matrix and the style matrices of the comparison images
    style_pairwise_distances = pairwise_distances(test_style_matrix, comparison_style_matrices)
    # Calculate the total distance based on the formula in Alexis's tutorial
    totals = content_pairwise_distances + (1000000 * style_pairwise_distances)
    # Get the array containing the distances
    distances = totals[0]
    # Use numpy's argsort function to create an array containing the indexes of distances in the order they need
    # to be in to sort the array lowest to highest
    sorted_order = np.argsort(distances)
    
    # Iterate through the array using sorted order to return the number of matches specified by the 'number_matches' parameter
    count = 0
    matched_images = list()
    for i in sorted_order:
        # Get the album index corresponding to the image index
        album_index = comparison_album_indexes[i]
        # Get one dataframe index corresponding to this image index. This dataframe index corresponds to an image name in
        # the 'Images' folder
        index = oramas_data[oramas_data['album_index'] == album_index].index[0]
        # Add the image index to 'matched_images' list
        matched_images.append(index)
        count += 1
        # If we've reached the number of images to match break out of the loop
        if count == number_matches:
            break
            
    return matched_images

In [7]:
# Load the following for the comparison images:
    # Content matrices
    # Style matrices
    # Album indexes
# All of these lists use the same indexing e.g. comparison_album_indexes[0] corresponds to comparison_content_matrices[0]
# which corresponds to comparison_style_matrices[0]
comparison_content_matrices = pickle.load(open('all_content_matrices_50_pca', 'rb'))
comparison_style_matrices = pickle.load(open('all_style_matrices_15_pca', 'rb'))
comparison_album_indexes = pickle.load(open('all_album_indexes', 'rb'))

In [8]:
# Create a loop to run through all the ethnicities and the images associated with them
# For every ethnicity, get the 10 closest images for every face
# WARNING: This code takes a VERY long time to run
image_folder = 'Face test dataset/fairface-img-margin025-trainval/'
face_dataset = pd.read_csv(face_test_folder+'fairface_label_train.csv').append(pd.read_csv(face_test_folder+'fairface_label_val.csv'))

# Group the face dataset by ethnicity
for ethnicity, grouped in face_dataset.groupby('race'):
    
    # Get the unique file names for this ethnicity
    files = grouped['file'].unique()
    total_files = len(files)
    seen_files = list()
    # If we haven't created the matching file for this ethnicity, create it
    if not os.path.exists('%s_top_10.txt' % ethnicity):
        open('%s_top_10.txt' % ethnicity, 'w').close()
    # If we have created the matching file for this ethnicity, open it and load all the images that we've previously processed
    else:
        seen_files = [line.split('\t')[0] for line in fileinput.input('%s_top_10.txt' % ethnicity)]
    print(ethnicity)
    # Open the file for appending
    with open('%s_top_10.txt' % ethnicity, 'a') as out:
        # Iterate through the files for this ethnicity
        for f in files:
            # If we've seen this file before, skip
            if f in seen_files:
                continue
            # Load the face image
            image = get_image('%s/%s' % (image_folder, f))
            # Get the top 10 matches for the face image
            image = torch.unsqueeze(image, 0)
            matches = get_closest(image, comparison_album_indexes, comparison_content_matrices, comparison_style_matrices, 10)
            # Write the matches
            out.write('%s\t%s\n' % (f,str(matches)))  
            count += 1

            # Maintain a count to keep track of progress
            if count % 100 == 0:
                print(count/total_files)
    

White


C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceT

C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceT

C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceT

C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceT

...

C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceT

C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceT

C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  import sys
C:\Users\amcgo\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceT

0.43520309477756286


NameError: name 'sys' is not defined